In [1]:
import os
import sys

In [8]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
import pickle
from skimage.filters import threshold_otsu
from scipy.ndimage import distance_transform_edt
from scipy.spatial import distance

In [6]:
import plotly
from plotly.graph_objs import graph_objs as go
import ipywidgets as widgets
#plotly.offline.init_notebook_mode(connected=True)
from plotly.offline import iplot

In [4]:

url = "https://raw.githubusercontent.com/plotly/datasets/master/gapminderDataFiveYear.csv"
dataset = pd.read_csv(url)

years = ["1952", "1962", "1967", "1972", "1977", "1982", "1987", "1992", "1997", "2002",
         "2007"]

# make list of continents
continents = []
for continent in dataset["continent"]:
    if continent not in continents:
        continents.append(continent)
# make figure
fig_dict = {
    "data": [],
    "layout": {},
    "frames": []
}

# fill in most of layout
fig_dict["layout"]["xaxis"] = {"range": [30, 85], "title": "Life Expectancy"}
fig_dict["layout"]["yaxis"] = {"title": "GDP per Capita", "type": "log"}
fig_dict["layout"]["hovermode"] = "closest"
fig_dict["layout"]["updatemenus"] = [
    {
        "buttons": [
            {
                "args": [None, {"frame": {"duration": 500, "redraw": False},
                                "fromcurrent": True, "transition": {"duration": 300,
                                                                    "easing": "quadratic-in-out"}}],
                "label": "Play",
                "method": "animate"
            },
            {
                "args": [[None], {"frame": {"duration": 0, "redraw": False},
                                  "mode": "immediate",
                                  "transition": {"duration": 0}}],
                "label": "Pause",
                "method": "animate"
            }
        ],
        "direction": "left",
        "pad": {"r": 10, "t": 87},
        "showactive": False,
        "type": "buttons",
        "x": 0.1,
        "xanchor": "right",
        "y": 0,
        "yanchor": "top"
    }
]

sliders_dict = {
    "active": 0,
    "yanchor": "top",
    "xanchor": "left",
    "currentvalue": {
        "font": {"size": 20},
        "prefix": "Year:",
        "visible": True,
        "xanchor": "right"
    },
    "transition": {"duration": 300, "easing": "cubic-in-out"},
    "pad": {"b": 10, "t": 50},
    "len": 0.9,
    "x": 0.1,
    "y": 0,
    "steps": []
}

# make data
year = 1952
for continent in continents:
    dataset_by_year = dataset[dataset["year"] == year]
    dataset_by_year_and_cont = dataset_by_year[
        dataset_by_year["continent"] == continent]

    data_dict = {
        "x": list(dataset_by_year_and_cont["lifeExp"]),
        "y": list(dataset_by_year_and_cont["gdpPercap"]),
        "mode": "markers",
        "text": list(dataset_by_year_and_cont["country"]),
        "marker": {
            "sizemode": "area",
            "sizeref": 200000,
            "size": list(dataset_by_year_and_cont["pop"])
        },
        "name": continent
    }
    fig_dict["data"].append(data_dict)

# make frames
for year in years:
    frame = {"data": [], "name": str(year)}
    for continent in continents:
        dataset_by_year = dataset[dataset["year"] == int(year)]
        dataset_by_year_and_cont = dataset_by_year[
            dataset_by_year["continent"] == continent]

        data_dict = {
            "x": list(dataset_by_year_and_cont["lifeExp"]),
            "y": list(dataset_by_year_and_cont["gdpPercap"]),
            "mode": "markers",
            "text": list(dataset_by_year_and_cont["country"]),
            "marker": {
                "sizemode": "area",
                "sizeref": 200000,
                "size": list(dataset_by_year_and_cont["pop"])
            },
            "name": continent
        }
        frame["data"].append(data_dict)

    fig_dict["frames"].append(frame)
    slider_step = {"args": [
        [year],
        {"frame": {"duration": 300, "redraw": False},
         "mode": "immediate",
         "transition": {"duration": 300}}
    ],
        "label": year,
        "method": "animate"}
    sliders_dict["steps"].append(slider_step)


fig_dict["layout"]["sliders"] = [sliders_dict]

fig = go.Figure(fig_dict)

fig.show()

In [7]:

fig = go.Figure(
    data=[go.Scatter(x=[0, 1], y=[0, 1])],
    layout=go.Layout(
        xaxis=dict(range=[0, 5], autorange=False),
        yaxis=dict(range=[0, 5], autorange=False),
        title="Start Title",
        updatemenus=[dict(
            type="buttons",
            buttons=[dict(label="Play",
                          method="animate",
                          args=[None])])]
    ),
    frames=[go.Frame(data=[go.Scatter(x=[1, 2], y=[1, 2])]),
            go.Frame(data=[go.Scatter(x=[1, 4], y=[1, 4])]),
            go.Frame(data=[go.Scatter(x=[3, 4], y=[3, 4])],
                     layout=go.Layout(title_text="End Title"))]
)

fig.show()

In [11]:
skel=pickle.load(open("skelSort.pkl","rb"))
dat=np.load(open('Ptraj0.npy',"rb"))

In [14]:
fig=go.Figure(
    data=[go.Scatter3d(
    x = dat[:, 0],
    y = dat[:, 1],
    z = dat[:, 2],
    mode='markers',
    marker=dict(
        size=1.75,
        color="cornflowerblue",                # set color to an array/list of desired values
        #colorscale='Viridis',   # choose a colorscale
        opacity=.9
    ),
    name='H0'

)]
)
fig.show()

In [23]:
alpha=.07
b1s=[np.array([s[0] for s in skel if len(s[0]) == 2 and s[1] <= alpha])]
triangles = np.array([s[0] for s in skel if len(s[0]) == 3 and s[1] <= alpha])


pts=go.Scatter3d(
    x = dat[:, 0],
    y = dat[:, 1],
    z = dat[:, 2],
    mode='markers',
    marker=dict(
        size=2,
        color="cornflowerblue",                # set color to an array/list of desired values
        #colorscale='Viridis',   # choose a colorscale
        opacity=.9
    ),
    name='H0'

)

sfig=[pts]

linepts={0:[],1:[],2:[]}
for i in b1s[0]:
    linepts[0].append(dat[i[0],0])
    linepts[1].append(dat[i[0],1])
    linepts[2].append(dat[i[0],2])
    linepts[0].append(dat[i[1],0])
    linepts[1].append(dat[i[1],1])
    linepts[2].append(dat[i[1],2])

    linepts[0].append(None)
    linepts[1].append(None)
    linepts[2].append(None)
#for i in range(3):
#        linepts[i]=np.array(linepts[i])


if len(linepts[0])>0:
    lins=go.Scatter3d(
        x=linepts[0],
        y=linepts[1],
        z=linepts[2],
        mode='lines',
        name='H1',
        marker=dict(
            size=3,
            color="#d55e00",                # set color to an array/list of desired values
            #colorscale='Viridis',   # choose a colorscale
            opacity=.9
        )
    )
    sfig.append(lins)
    if len(triangles)>0:
        mesh = go.Mesh3d(
            x = dat[:, 0],
            y = dat[:, 1],
            z = dat[:, 2],
            i = triangles[:, 0],
            j = triangles[:, 1],
            k = triangles[:, 2],
            color="#009e73",
            opacity=.75,
            name='H2'
        )


        sfig.append(mesh)
fig=go.Figure(sfig,layout=go.Layout(
    width=1000,height=1000
    ,
))

fig.show()


In [24]:

res=.05
maxRes=20



pts=go.Scatter3d(
    x = dat[:, 0],
    y = dat[:, 1],
    z = dat[:, 2],
    mode='markers',
    marker=dict(
        size=2,
        color="cornflowerblue",                # set color to an array/list of desired values
        #colorscale='Viridis',   # choose a colorscale
        opacity=.9
    ),
    name='H0'

)

sfig=[pts]







AttributeError: 'Figure' object has no attribute 'copy'

In [ ]:
fig = go.Figure(
    data=[go.Scatter(x=[0, 1], y=[0, 1])],
    layout=go.Layout(
        xaxis=dict(range=[0, 5], autorange=False),
        yaxis=dict(range=[0, 5], autorange=False),
        title="Start Title",
        updatemenus=[dict(
            type="buttons",
            buttons=[dict(label="Play",
                          method="animate",
                          args=[None])])]
    ),
    frames=[go.Frame(data=[go.Scatter(x=[1, 2], y=[1, 2])]),
            go.Frame(data=[go.Scatter(x=[1, 4], y=[1, 4])]),
            go.Frame(data=[go.Scatter(x=[3, 4], y=[3, 4])],
                     layout=go.Layout(title_text="End Title"))]
)

fig.show()